##Alaskan Snow Model

This code was written by Sam Neitlich but some pieces were taken from other sources (primarily stack overflow and github). The goal of this project was to create a landscape-scale snowpack model in Alaskan national parks. In this model, snow water equivilant (SWE) was predicted on the basis of PRISM temperature and precipitation. Meaured SWE data from SNOTEL sites was also used to train and validate the model. This script focuses on preparing the input data, and the actual model is fit and tested in R (that file is also attached).This Alaskan snowpack model was based on [this](https://onlinelibrary.wiley.com/doi/epdf/10.1002/hyp.8176?saml_referrer) paper by Leibowitz et al., which used the same model to predict SWE across the state of Oregon. The same approach was also used in [this](https://onlinelibrary.wiley.com/doi/pdf/10.1111/1752-1688.12544?saml_referrer) paper by Todd et al., which used this model in southern Alaska.

This code was written and compiled in Google Colab, which is free to use with a Google account. That said, it can be easily modified to run in other IDE's such as Jupyter Notebooks or VS Code. 



##Part 1: SNOTEL Site Query

In this section, I used an approach based on the NASA SnowEx hackweek to filter out relevant SNOTEL sites and compile a list of monthly SWE values. Because the PRISM data is calculated in monthly 30 year normals, the SNOTEL SWE data was also formatted in this way. This data was used as a validation for the final model, and was converted to units of mm. 
https://snowex-hackweek.github.io/website/tutorials/geospatial/SNOTEL_query.html

In [1]:
#This is the latest CUAHSI API endpoint
wsdlurl = 'https://hydroportal.cuahsi.org/Snotel/cuahsi_1_1.asmx?WSDL'

In [2]:
#Install the required libraries libraries
%%capture
# %%capture hides most of the outputs, just make sure your code is correct!
!pip install geopandas -q # the -q makes it quiet (does not show all of the loading)
!pip install fiona -q
!pip install pyproj -q
!pip install ulmo -q 
!pip install geoviews -q
!pip install contextily -q
!pip install geoplot -q
!pip install folium

In [3]:
##import the necessary libaries and packages. If any of the do not work you will need to install them. 
import os
from datetime import datetime
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import geopandas as gpd
import geoplot as gplt
import geoplot.crs as gcrs
from shapely.geometry import Point
import contextily as ctx
import ulmo
import fiona
from IPython.display import HTML
from pyproj import CRS
import contextily as cx
import folium

In [6]:
sites = ulmo.cuahsi.wof.get_sites(wsdlurl) #Grab site metadata from server
sites_df = pd.DataFrame.from_dict(sites, orient='index').dropna() #create dataframe with all sites and drop null values
sites_df['geometry'] = [Point(float(loc['longitude']), float(loc['latitude'])) for loc in sites_df['location']] #add point feature to df

sites_df = sites_df.drop(columns='location') #Drop unnecessary columns
sites_df = sites_df.astype({"elevation_m":float}) #First convert to a float
sites_df['elevation_m'] = sites_df['elevation_m'].astype(int) #Convert elevation to a integer 
sites_df.head() #Print out first few snotel sites--the sites are organized alphabetically based on name

/usr/local/lib/python3.7/dist-packages/pandas/core/dtypes/cast.py:118: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  arr = construct_1d_object_array_from_listlike(values)


code            name network  elevation_m  \
SNOTEL:301_CA_SNTL    301_CA_SNTL        Adin Mtn  SNOTEL         1886   
SNOTEL:907_UT_SNTL    907_UT_SNTL     Agua Canyon  SNOTEL         2712   
SNOTEL:916_MT_SNTL    916_MT_SNTL      Albro Lake  SNOTEL         2529   
SNOTEL:1267_AK_SNTL  1267_AK_SNTL  Alexander Lake  SNOTEL           48   
SNOTEL:908_WA_SNTL    908_WA_SNTL  Alpine Meadows  SNOTEL         1066   

                                                         site_property  \
SNOTEL:301_CA_SNTL   {'county': 'Modoc', 'state': 'California', 'si...   
SNOTEL:907_UT_SNTL   {'county': 'Kane', 'state': 'Utah', 'site_comm...   
SNOTEL:916_MT_SNTL   {'county': 'Madison', 'state': 'Montana', 'sit...   
SNOTEL:1267_AK_SNTL  {'county': 'Matanuska-Susitna', 'state': 'Alas...   
SNOTEL:908_WA_SNTL   {'county': 'King', 'state': 'Washington', 'sit...   

                                                           geometry  
SNOTEL:301_CA_SNTL     POINT (-120.79192352294922 41.2358283996582)  
SNOTEL:907_UT_SNTL    POINT (-112.27117919921875 37.52217102050781)  
SNOTEL:916_MT_SNTL    POINT (-111.95902252197266 45.59722900390625)  
SNOTEL:1267_AK_SNTL   POINT (-150.88966369628906 61.74966812133789)  
SNOTEL:908_WA_SNTL   POINT (-121.69847106933594 47.779571533203125)

In [7]:
#Create a geodataframe with the sites and project it to NAD 83, which is what the PRISM data is in.
sites_gdf_all = gpd.GeoDataFrame(sites_df, crs='EPSG:4326') #First project the data to WGS 84
sites_gdf_all = sites_gdf_all.to_crs(epsg=4269) #Reproject to NAD 83

print(sites_gdf_all.crs) #Double check that the data is in the right CRS

#The data is ready to be plotted. 

epsg:4269


In [8]:
#Load in two watershed boundaries from github. "?raw=true" needs to be pasted at the end of the url for this to work.
HUC8Bound = gpd.read_file('https://github.com/samsamsam34/AKSnowModel/blob/218335c6490a783e72f1eb35b11b8cbc376b231c/SiteBoundaryHUC8.geojson?raw=true')
HUC6Bound = gpd.read_file('https://github.com/samsamsam34/AKSnowModel/blob/218335c6490a783e72f1eb35b11b8cbc376b231c/SiteBoundaryHUC6.geojson?raw=true')

Expecting property name enclosed in double quotes: line 1 column 2 (char 1)
Expecting property name enclosed in double quotes: line 1 column 2 (char 1)


In [9]:
#Check to make sure that all of the layers are in the same CRS
print(HUC8Bound.crs)
print(HUC6Bound.crs)
print(sites_gdf_all.crs)

epsg:4269
epsg:4269
epsg:4269


In [10]:
HUC6Bound.iloc[0] #Convert to a GeoSeries

OBJECTID                                                             1
tnmid                           {4668D3D5-50BC-41B2-A100-72F60B3AE14A}
metasourceid                                                      None
sourcedatadesc                                                    None
sourceoriginator                                                  None
sourcefeatureid                                                   None
loaddate                                                 1616419983000
referencegnis_ids                                                 None
areaacres                                                   28560754.3
areasqkm                                                     115581.37
states                                                           AK,CN
huc6                                                            190803
name                                                      Tanana River
Shape_Length                                                 51.193671
Shape_

In [11]:
#Save the geometry of each geoSeries to a new variable
HUC6_geom = HUC6Bound.iloc[0].geometry #HUC 6 watershed boundary
HUC8_geom = HUC8Bound.iloc[0].geometry #HUC 8 watershed boundary

HUC6_geom #Print out to verify that it worked

In [12]:
#Creates an index that shows whether a SNOTEL site is in each of these watersheds
idxHUC6 = sites_gdf_all.intersects(HUC6_geom) #This essentially indicates whether each site intersects the geometry defined above
idxHUC8 = sites_gdf_all.intersects(HUC8_geom)

In [13]:
idxHUC6.head() #Print the head, we can see that none of these sites are in the HUC 6 watershed

SNOTEL:301_CA_SNTL     False
SNOTEL:907_UT_SNTL     False
SNOTEL:916_MT_SNTL     False
SNOTEL:1267_AK_SNTL    False
SNOTEL:908_WA_SNTL     False
dtype: bool

In [14]:
idxHUC6.value_counts() #There are 12 SNOTEL sites in the HUC 6 watershed

False    918
True      12
dtype: int64

In [15]:
idxHUC8.value_counts()#There are 7 SNOTEL sites in the HUC 8 watershed

False    923
True       7
dtype: int64

In [16]:
# the idx grabs the true/false of the Boolean quesry for HUC6 and HUC8 SNOTEL sites.
# We will now create a new dataframe using the index
# This will be done for both the HUC 6 SNOTEL sites and the HUC 8 SNOTEL sites

HUC6_snotel_sites = sites_gdf_all.loc[idxHUC6]
HUC8_snotel_sites = sites_gdf_all.loc[idxHUC8]
HUC6_snotel_sites.head()

code            name network  elevation_m  \
SNOTEL:1093_AK_SNTL  1093_AK_SNTL         Chisana  SNOTEL         1011   
SNOTEL:1174_AK_SNTL  1174_AK_SNTL  Fairbanks F.O.  SNOTEL          137   
SNOTEL:1268_AK_SNTL  1268_AK_SNTL   Fielding Lake  SNOTEL          914   
SNOTEL:963_AK_SNTL    963_AK_SNTL     Granite Crk  SNOTEL          377   
SNOTEL:1072_AK_SNTL  1072_AK_SNTL       Kantishna  SNOTEL          472   

                                                         site_property  \
SNOTEL:1093_AK_SNTL  {'county': 'Valdez-Cordova', 'state': 'Alaska'...   
SNOTEL:1174_AK_SNTL  {'county': 'Fairbanks North Star', 'state': 'A...   
SNOTEL:1268_AK_SNTL  {'county': 'Valdez-Cordova', 'state': 'Alaska'...   
SNOTEL:963_AK_SNTL   {'county': 'Southeast Fairbanks', 'state': 'Al...   
SNOTEL:1072_AK_SNTL  {'county': 'Denali', 'state': 'Alaska', 'site_...   

                                        geometry  
SNOTEL:1093_AK_SNTL  POINT (-142.04900 62.06900)  
SNOTEL:1174_AK_SNTL  POINT (-147.80000 64.85000)  
SNOTEL:1268_AK_SNTL  POINT (-145.63049 63.20267)  
SNOTEL:963_AK_SNTL   POINT (-145.39993 63.94382)  
SNOTEL:1072_AK_SNTL  POINT (-150.99400 63.54167)

In [17]:
#This saves the file in Colab -- this will come in handy later
sites_fn = 'HUC6_snotel_sites.json'
if not os.path.exists(sites_fn):
    HUC6_snotel_sites.to_file(sites_fn, driver='GeoJSON')

    ## Look over in your files on the left. The geojson file should have saved. 

In [18]:
# Create colormap with min/max elevation
# https://notebook.community/ocefpaf/folium/examples/Colormaps for more options
import branca.colormap as cm
elev_min = HUC6_snotel_sites.elevation_m.min()
elev_max = HUC6_snotel_sites.elevation_m.max()
cmap = cm.linear.BrBG_08.scale(elev_min, elev_max)
cmap.caption = 'Elevation [m]'

# Create map
snotel_map = folium.Map(location=[64, -147], zoom_start=6, 
                        tiles='Stamen terrain', control_scale=True)

# Create Marker Cluster layer
from folium.plugins import MarkerCluster
cluster = MarkerCluster(name='SNOTEL stations')

# Add points as Markers into MarkerCluster layer
for idx in HUC6_snotel_sites.index:
    pt = HUC6_snotel_sites.loc[idx]
    # Need to extract lat/lon from geometry
    # CircleMarker expects ordered pair, not GeoJSON
    yy = pt.geometry.y
    xx = pt.geometry.x
    color = cmap(pt.elevation_m)
    # Add point
    folium.CircleMarker(
        location=(yy, xx),
        color='black',
        weight=2,
        fill=True,
        fill_color=color,
        fill_opacity=1.0).add_to(cluster)
# Add MarkerCluster layer to map
cluster.add_to(snotel_map)
# Add colorbar to map
snotel_map.add_child(cmap)
# Add Montana polygon to map, if needed
snotel_map.add_child(folium.GeoJson(HUC6Bound, name='HUC6 Study Area'))
snotel_map.add_child(folium.GeoJson(HUC8Bound, name='HUC8 Study Area'))

snotel_map.add_child(folium.LayerControl())
snotel_map

In [ ]:
#Since the HUC 6 has more sites, we will focus on that for now. 

In [17]:
#!pip install basemap -q

In [20]:
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt
#from mpl_toolkits.basemap import Basemap

In [21]:
variablecode = 'SNOTEL:WTEQ_D' #We are looking for daily SWE (WETQ_D) values

In [22]:
ulmo.cuahsi.wof.get_variable_info(wsdlurl, variablecode) #This shows the variable info. Units are inches

{'code': 'WTEQ_D',
 'data_type': 'Continuous',
 'general_category': 'Soil',
 'id': '310',
 'name': 'Snow water equivalent',
 'no_data_value': '-9999',
 'sample_medium': 'Snow',
 'speciation': 'Not Applicable',
 'time': {'interval': '1',
  'is_regular': True,
  'units': {'abbreviation': 'd',
   'code': '104',
   'name': 'day',
   'type': 'Time'}},
 'units': {'abbreviation': 'in',
  'code': '49',
  'name': 'international inch',
  'type': 'Length'},
 'value_type': 'Field Observation',
 'vocabulary': 'SNOTEL'}

In [23]:
#Get current datetime
today = datetime.today().strftime('%Y-%m-%d')
#Define function to grab data
def snotel_fetch(sitecode, variablecode='SNOTEL:WTEQ_D', start_date='1950-10-01', end_date=today):
    #print(sitecode, variablecode, start_date, end_date)
    values_df = None
    try:
        #Request data from the server
        site_values = ulmo.cuahsi.wof.get_values(wsdlurl, sitecode, variablecode, start=start_date, end=end_date)
        #Convert to a Pandas DataFrame   
        values_df = pd.DataFrame.from_dict(site_values['values'])
        #Parse the datetime values to Pandas Timestamp objects
        values_df['datetime'] = pd.to_datetime(values_df['datetime'], utc=True)
        #Set the DataFrame index to the Timestamps
        values_df = values_df.set_index('datetime')
        #Convert values to float and replace -9999 nodata values with NaN
        values_df['value'] = pd.to_numeric(values_df['value']).replace(-9999, np.nan)
        #Remove any records flagged with lower quality
        values_df = values_df[values_df['quality_control_level_code'] == '1']
    except:
        print("Unable to fetch %s" % variablecode)

    return values_df

In [24]:
from pandas.api.types import CategoricalDtype

In [25]:
# Order the months with October as the first entry. This is useful because October 1st is the start of the 
# water year and previous SWE is usually 0.

month_order = CategoricalDtype([10,11,12,1,2,3,4,5,6,7,8,9], ordered=True) 
#This can later be used to reorder dataframes

In [26]:
#Define an empty dataframe to store returns for each site

outDF = pd.DataFrame() 

for i, sitecode in enumerate(HUC6_snotel_sites.index): #Iterate through every snotel site in the HUC 6 boundary
    print('%i of %i sites: %s' % (i+1, len(HUC6_snotel_sites.index), sitecode)) #Print each site
    out = snotel_fetch(sitecode, variablecode) #Call the fetch function defined above, assign output to new dataframe
    if out is not None: #Make sure that the data exists
      out['month'] =  out.date_time_utc.str[5:7] #Extract the month and add it to the dataframe
      out = out[out['value'].notna()] #Drop all null values

      out = out.astype({"month": int}) #Convert the month to an integer
      monthlyMean = out.groupby(['month']).mean() #Group by month and calculate the mean
      #This gives us a mean over all records (usually close to 30 years) for each month, therefore matching the format of PRISM
      monthlyMean['site'] = HUC6_snotel_sites.code[i][:-8] #Add the site name to the dataframe
      monthlyMean = monthlyMean.reset_index() #Reset index
      monthlyMean['month'] = monthlyMean['month'].astype(month_order) #Reorder the dataframe (see previous cell)
      monthlyMean = monthlyMean.sort_values('month') #Reorder the dataframe

      outDF = outDF.append(monthlyMean) #Append the values of each site to the final output dataframe
      #This will give us a sorted dataframe with the mean SWE for each month and each site


1 of 12 sites: SNOTEL:1093_AK_SNTL
2 of 12 sites: SNOTEL:1174_AK_SNTL
3 of 12 sites: SNOTEL:1268_AK_SNTL
4 of 12 sites: SNOTEL:963_AK_SNTL
5 of 12 sites: SNOTEL:1072_AK_SNTL
6 of 12 sites: SNOTEL:947_AK_SNTL
7 of 12 sites: SNOTEL:949_AK_SNTL
8 of 12 sites: SNOTEL:948_AK_SNTL
9 of 12 sites: SNOTEL:950_AK_SNTL
10 of 12 sites: SNOTEL:1178_AK_SNTL


Unable to fetch SNOTEL:WTEQ_D
11 of 12 sites: SNOTEL:951_AK_SNTL
12 of 12 sites: SNOTEL:952_AK_SNTL


In [27]:
outDF.set_index('month', inplace=True) #Set the index to month
outDF = outDF[['site', 'value']] #Switch the order of columns -- not too important

outDF = outDF.rename(columns={'value': 'SWE'}) #Rename columns
outDF['SWE'] *= 25.4 #Convert SWE from inches to mm

outDF.head() #Print first 5 values

site        SWE
month                 
10     1093   9.873226
11     1093  24.565429
12     1093  44.648986
1      1093  58.554608
2      1093  74.155139

##Section 2: Read in PRISM data and extract monthly mean temperature and precipitation values

Now that we have all of the SWE data, we are ready to extract the PRISM temperature and precipitation that correspond to each site. This code section will grab data from the PRISM website and extract raster values by location, thereby giving us the monthly precipitation and temperature values at each of these sites. These are all 30 year normals and are collected for each month. Prism uses degrees C for temperature and mm for precipitation. All values of precipitation, PET, and SWE will be calculated in mm. 

https://prism.oregonstate.edu/projects/alaska.php


In [28]:
#Some of these libraries are duplicates from above, but the goal is that these sections could be run independantly

%%capture
!pip install --upgrade geopandas -q
!pip install mapclassify -q
!pip install --upgrade datascience -q
!pip install --upgrade gym -q
!pip install raster_tools -q
!pip install graphviz -q
!pip install rasterio -q
!pip install gdal -q
!pip install contextily -q

In [29]:
import os
import gdal
from glob import glob
import numpy
import rasterio
from rasterio.plot import show
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import geopandas as gpd
from rasterio.plot import show_hist
import contextily as ctx
from osgeo import gdal, osr

In [30]:
#Rename output dataframe to swe and change some variable types
swe = outDF
swe = swe.astype({"site":int}) #Change site to an integer
swe['PRISM_Temp'] = numpy.NaN #Add an empty column to dataframe
swe.head() #Print first 5 values

site        SWE  PRISM_Temp
month                             
10     1093   9.873226         NaN
11     1093  24.565429         NaN
12     1093  44.648986         NaN
1      1093  58.554608         NaN
2      1093  74.155139         NaN

In [31]:
HUC6Sites = gpd.read_file('HUC6_snotel_sites.json') #Read in the HUC 6 SNOTEL sites that we saved earlier
#We could use the geodataframe from before but this is a good demonstration of how to read in a file in Colab

count=0 #Set counter
for j in HUC6Sites.code: #Iterate through each HUC 6 SNOTEL site by code
  site = HUC6Sites['code'][count][:-8] #Isolate the four digit site code
  if int(site) not in swe['site'].unique(): #Compare the specific SNOTEL site to the list of sites in the SWE dataframe
    site_update = site + '_AK_SNTL' #Create the full string used in the geodataframe
    HUC6Sites = HUC6Sites[HUC6Sites.code != site_update] #Remove any sites not in the swe dataframe from the HUC6Sites dataframe
  count +=1 #Increment counter by 1 each time

#This code accounts for any sites where the SWE values could not be extracted and removes them from the HUC 6 Sites geodataframe
#For example, we were not able to fetch any data from site number 10 (1178_AK_SNTL), so this was removed.
HUC6Sites.head()

index          code            name network  elevation_m  \
0  SNOTEL:1093_AK_SNTL  1093_AK_SNTL         Chisana  SNOTEL         1011   
1  SNOTEL:1174_AK_SNTL  1174_AK_SNTL  Fairbanks F.O.  SNOTEL          137   
2  SNOTEL:1268_AK_SNTL  1268_AK_SNTL   Fielding Lake  SNOTEL          914   
3   SNOTEL:963_AK_SNTL   963_AK_SNTL     Granite Crk  SNOTEL          377   
4  SNOTEL:1072_AK_SNTL  1072_AK_SNTL       Kantishna  SNOTEL          472   

                                       site_property  \
0  {'county': 'Valdez-Cordova', 'state': 'Alaska'...   
1  {'county': 'Fairbanks North Star', 'state': 'A...   
2  {'county': 'Valdez-Cordova', 'state': 'Alaska'...   
3  {'county': 'Southeast Fairbanks', 'state': 'Al...   
4  {'county': 'Denali', 'state': 'Alaska', 'site_...   

                      geometry  
0  POINT (-142.04900 62.06900)  
1  POINT (-147.80000 64.85000)  
2  POINT (-145.63049 63.20267)  
3  POINT (-145.39993 63.94382)  
4  POINT (-150.99400 63.54167)

In [32]:
def adjust_coordinates(fname): #Define a function that adjusts the coordinates of the PRISM data based on filename
  with open(fname, 'r') as f: #Open the file to read 
    line1 = f.readline() #Read the first two lines, save to variables
    line2 = f.readline()

    x = f.readline() #Save the third line -- this one will be edited
    text = x[:10] #Save the text 
    value = str(float(x[10:])-360) #Save the numeric value to be edited and edit it
    #The longitude values all come in 360 degrees to the right, so the center of Alaska was around +200 rather than -160 (or so)
    fullLine = text + value +'\n' #Combine text and new file

    lines = [] #Create empty list
    # read file

    # read an store all lines into list
    lines = f.readlines()

    f.close() #Close file

  # Write file
  with open(fname, 'w') as fp: #Reopen the file, in writing mode this time
    #Write the first two lines to file
    fp.write(line1)
    fp.write(line2)

    #Append the new line to the file
    fp.write(fullLine)

    # iterate each line
    for number, line in enumerate(lines):
        #Write each line to file
        fp.write(line)

    fp.close() #Close the file writer
    return fname #Return the name of the file

In [33]:
#Define a function to extract PRISM data
def read_PRISM(input_file, swe_data, snotel_sites, month): #Takes in dataframe with SWE measurements and adds PRISM Temp
  drv = gdal.GetDriverByName('GTiff') #This block of code reads in the PRISM text files and saves to a temporary tif file
  ds_in = gdal.Open(input_file)
  ds_out = drv.CreateCopy('projTemp.tif', ds_in)
  srs = osr.SpatialReference()
  srs.ImportFromEPSG(4269) #Set projection to NAD 83 (per PRISM website)
  ds_out.SetProjection(srs.ExportToWkt())
  ds_in = None
  ds_out = None

  temps = rasterio.open('projTemp.tif') #Open the raster and save to temps

  count = 0
  for point in snotel_sites['geometry']: #Iterate through each SNOTEL site
      x = point.xy[0][0] #Save lat and lon from each SNOTEL site
      y = point.xy[1][0]
      row, col = temps.index(x,y) #Grab PRISM pixel value where a SNOTEL site is
      site = snotel_sites.iloc[count][1][:-8] #Save the site name
      swe_data.loc[((swe_data['month']==month) & (swe_data['site']== int(site))), 'PRISM_Temp'] = temps.read(1)[row,col]
      #Add the month, site number, and PRISM temperature to the input dataframe
      count+=1 

  return swe_data #Return the updated dataframe

In [34]:
!wget -r -l 2 https://prism.oregonstate.edu/projects/public/alaska/grids/ -q 
#This command grabs the subfolders from the PRISM website and saves them locally
#We can therefore access the PRISM data without having to download large files

In [32]:
#!rm -rf /content/prism.oregonstate.edu #This removes the folder -- doesn't need to be used

In [35]:
import os, zipfile
import shutil

#This code block unzips each temperature file and saves it to content (on the left)
dir_name = '/content/prism.oregonstate.edu/projects/public/alaska/grids/tmean/' #Directory where temperature data is saved
extension = ".zip" #Date comes in as a zip file for each month

os.chdir(dir_name) # change directory from working dir to dir with files

for item in os.listdir(dir_name): # loop through items in dir
    if item.endswith(extension): # check for ".zip" extension
        file_name = os.path.abspath(item) # get full path of files
        zip_ref = zipfile.ZipFile(file_name) # create zipfile object
        zip_ref.extractall('/content/') # extract file to dir, the output directory can be changed if desired
        #shutil.move(zip_ref, "/content/")

        zip_ref.close() # close file
        os.remove(file_name) # delete zipped file

In [36]:
swe.reset_index(inplace=True) #Reset index

In [37]:
for i in range (1,13): #Iterate through each month
  filename = '/content/ak_tmean_1981_2010.' + str(i).zfill(2) +'.txt' #Specify the full filename
  adj_file = adjust_coordinates(filename) #Adjust the coordinates of each file
  adj_file = filename 
  final_data = read_PRISM(adj_file, swe, HUC6Sites, i) #Call the function from earlier to extract temperature data by site

final_data #Print out final data

month  site        SWE  PRISM_Temp
0      10  1093   9.873226   -6.295001
1      11  1093  24.565429  -17.150002
2      12  1093  44.648986  -20.220001
3       1  1093  58.554608  -21.640001
4       2  1093  74.155139  -16.600000
..    ...   ...        ...         ...
127     5   952  57.666150    4.605000
128     6   952   0.324556   11.695000
129     7   952   0.000000   11.425000
130     8   952   0.000000    8.675000
131     9   952   2.282701    3.510000

[132 rows x 4 columns]

In [38]:
#Redefine this function to extract precipitation rather than temperature--roughly the same as above
def read_PRISM(input_file, swe_data, snotel_sites, month):
  drv = gdal.GetDriverByName('GTiff')
  ds_in = gdal.Open(input_file)
  ds_out = drv.CreateCopy('projTemp.tif', ds_in)
  srs = osr.SpatialReference()
  srs.ImportFromEPSG(4269) #NAD 83
  ds_out.SetProjection(srs.ExportToWkt())
  ds_in = None
  ds_out = None

  precip = rasterio.open('projTemp.tif')

  count = 0
  for point in snotel_sites['geometry']:
      x = point.xy[0][0]
      y = point.xy[1][0]
      row, col = precip.index(x,y)
      site = snotel_sites.iloc[count][1][:-8]
      swe_data.loc[((swe_data['month']==month) & (swe_data['site']== int(site))), 'PRISM_Ppt'] = precip.read(1)[row,col]
      count+=1

  return swe_data

In [39]:
import os, zipfile
import shutil

#Unzip precipitation files again -- same as above
dir_name = '/content/prism.oregonstate.edu/projects/public/alaska/grids/ppt/'
extension = ".zip"

os.chdir(dir_name) # change directory from working dir to dir with files

for item in os.listdir(dir_name): # loop through items in dir
    if item.endswith(extension): # check for ".zip" extension
        file_name = os.path.abspath(item) # get full path of files
        zip_ref = zipfile.ZipFile(file_name) # create zipfile object
        zip_ref.extractall('/content/') # extract file to dir
        #shutil.move(zip_ref, "/content/")

        zip_ref.close() # close file
        os.remove(file_name) # delete zipped file

In [40]:
for i in range (1,13): #Same as above -- iterate through all files and add precipitation data to final dataframe
  filename = '/content/ak_ppt_1981_2010.' + str(i).zfill(2) +'.txt'
  adj_file = adjust_coordinates(filename)
  adj_file = filename
  final_data = read_PRISM(adj_file, swe, HUC6Sites, i)

final_data

month  site        SWE  PRISM_Temp   PRISM_Ppt
0      10  1093   9.873226   -6.295001   23.601002
1      11  1093  24.565429  -17.150002   20.528002
2      12  1093  44.648986  -20.220001   17.347000
3       1  1093  58.554608  -21.640001   20.372002
4       2  1093  74.155139  -16.600000   17.749001
..    ...   ...        ...         ...         ...
127     5   952  57.666150    4.605000   30.607002
128     6   952   0.324556   11.695000   75.126007
129     7   952   0.000000   11.425000  101.633003
130     8   952   0.000000    8.675000   98.564003
131     9   952   2.282701    3.510000   56.733002

[132 rows x 5 columns]

In [ ]:
#We can see that there is a wide range of variation in precipitation and temperature, both by month and site.

#Part 3: Calculating Surplus

In this section, I calculate the surplus of the snowpack based on the equations from Leibowitz et al. (linked above). Surplus (precipitation - potential evapotranspiration (PET)) measures the amount of extra water available in the system. This is typically a positive number (indicating excess water) in the winter and a negative (indicating that there's less P than PET) in the summer. This calculation also involves a daylight hour calculation and a PET calculation.

In [41]:
import pandas as pd
#Read in a file of julian dates from github
url = 'https://github.com/samsamsam34/AKSnowModel/blob/d9a28bc184bcc61a78e2ec50703acb35c5ef5c5a/julian.csv?raw=true'

julian = pd.read_csv(url) #Save to dataframe

julian['days'] = julian['Julian End'] - julian['Julian Start'] +1 #Calculate number of days in each month
julian

month  Julian Start  Julian End  Julian Center  days
0       1             1          31             16    31
1       2            32          59             46    28
2       3            60          90             75    31
3       4            91         120            106    30
4       5           121         151            136    31
5       6           152         181            167    30
6       7           182         212            197    31
7       8           213         243            228    31
8       9           244         273            259    30
9      10           274         304            289    31
10     11           305         334            320    30
11     12           335         365            350    31

In [42]:
from pandas.api.types import CategoricalDtype
#Same categorical type as above
month_order = CategoricalDtype(
    [10,11,12,1,2,3,4,5,6,7,8,9], 
    ordered=True
)
#Order julian dates by wateryear month orders
julian['month'] = julian['month'].astype(month_order)
julian = julian.sort_values('month')

julian

month  Julian Start  Julian End  Julian Center  days
9     10           274         304            289    31
10    11           305         334            320    30
11    12           335         365            350    31
0      1             1          31             16    31
1      2            32          59             46    28
2      3            60          90             75    31
3      4            91         120            106    30
4      5           121         151            136    31
5      6           152         181            167    30
6      7           182         212            197    31
7      8           213         243            228    31
8      9           244         273            259    30

In [43]:
!pip install geopandas -q #-q is quiet, and minimizes the output

In [44]:
import geopandas as gpd
import numpy as np

snotel_sites = HUC6_snotel_sites #Create copy of HUC 6 sites


snotel_sites['lat'] = snotel_sites.geometry.y #Add the site latitude to the dataframe, this will be used in the daylight hours calculation
snotel_sites.head()

/usr/local/lib/python3.7/dist-packages/geopandas/geodataframe.py:1351: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


code            name network  elevation_m  \
SNOTEL:1093_AK_SNTL  1093_AK_SNTL         Chisana  SNOTEL         1011   
SNOTEL:1174_AK_SNTL  1174_AK_SNTL  Fairbanks F.O.  SNOTEL          137   
SNOTEL:1268_AK_SNTL  1268_AK_SNTL   Fielding Lake  SNOTEL          914   
SNOTEL:963_AK_SNTL    963_AK_SNTL     Granite Crk  SNOTEL          377   
SNOTEL:1072_AK_SNTL  1072_AK_SNTL       Kantishna  SNOTEL          472   

                                                         site_property  \
SNOTEL:1093_AK_SNTL  {'county': 'Valdez-Cordova', 'state': 'Alaska'...   
SNOTEL:1174_AK_SNTL  {'county': 'Fairbanks North Star', 'state': 'A...   
SNOTEL:1268_AK_SNTL  {'county': 'Valdez-Cordova', 'state': 'Alaska'...   
SNOTEL:963_AK_SNTL   {'county': 'Southeast Fairbanks', 'state': 'Al...   
SNOTEL:1072_AK_SNTL  {'county': 'Denali', 'state': 'Alaska', 'site_...   

                                        geometry        lat  
SNOTEL:1093_AK_SNTL  POINT (-142.04900 62.06900)  62.069000  
SNOTEL:1174_AK_SNTL  POINT (-147.80000 64.85000)  64.849998  
SNOTEL:1268_AK_SNTL  POINT (-145.63049 63.20267)  63.202671  
SNOTEL:963_AK_SNTL   POINT (-145.39993 63.94382)  63.943821  
SNOTEL:1072_AK_SNTL  POINT (-150.99400 63.54167)  63.541672

In [45]:
#Define a function to calculate the hours of daylight based on latitude and julian date
def day_length(J, L):

  #These calculations follow Forsythe et al. 
  #https://citeseerx.ist.psu.edu/viewdoc/download?doi=10.1.1.1083.5019&rep=rep1&type=pdf

  #Calculate value for each row and save to new column of dataframe
  revolution_angle = 0.2163108 + 2*(np.arctan(0.9671396*np.tan(0.00860*(J-186))))
  declination_angle = np.arcsin(0.39795 * np.cos(revolution_angle))
  numerator = np.sin(0.833*np.pi/180) + np.sin(L*np.pi/180) * np.sin(declination_angle)
  denominator = np.cos(L*np.pi/180)* np.cos(declination_angle)
  daylight_hours = 24 - 24/np.pi*np.arccos(numerator/denominator)

  daylight_hours /= 12 #The PET equation needs units of 12 hours
  return daylight_hours

In [46]:
snotel_sites['site'] = snotel_sites.code.str[:-8] #Add the site name and convert to an integer
snotel_sites['site'] = snotel_sites['site'].astype(int)

/usr/local/lib/python3.7/dist-packages/geopandas/geodataframe.py:1351: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


In [47]:
data = final_data #Rename dataframe for later use

data

month  site        SWE  PRISM_Temp   PRISM_Ppt
0      10  1093   9.873226   -6.295001   23.601002
1      11  1093  24.565429  -17.150002   20.528002
2      12  1093  44.648986  -20.220001   17.347000
3       1  1093  58.554608  -21.640001   20.372002
4       2  1093  74.155139  -16.600000   17.749001
..    ...   ...        ...         ...         ...
127     5   952  57.666150    4.605000   30.607002
128     6   952   0.324556   11.695000   75.126007
129     7   952   0.000000   11.425000  101.633003
130     8   952   0.000000    8.675000   98.564003
131     9   952   2.282701    3.510000   56.733002

[132 rows x 5 columns]

In [48]:
data = pd.merge(data,snotel_sites[['site','lat']],on='site', how='left') #Add latitude to the dataframe
data.head()

month  site        SWE  PRISM_Temp  PRISM_Ppt     lat
0    10  1093   9.873226   -6.295001  23.601002  62.069
1    11  1093  24.565429  -17.150002  20.528002  62.069
2    12  1093  44.648986  -20.220001  17.347000  62.069
3     1  1093  58.554608  -21.640001  20.372002  62.069
4     2  1093  74.155139  -16.600000  17.749001  62.069

In [49]:
data = pd.merge(data,julian[['month','Julian Center']],on='month', how='left') #Add days in month and Julian date for each site to dataframe
data = pd.merge(data,julian[['month','days']],on='month', how='left')
data.head()

month  site        SWE  PRISM_Temp  PRISM_Ppt     lat  Julian Center  days
0    10  1093   9.873226   -6.295001  23.601002  62.069            289    31
1    11  1093  24.565429  -17.150002  20.528002  62.069            320    30
2    12  1093  44.648986  -20.220001  17.347000  62.069            350    31
3     1  1093  58.554608  -21.640001  20.372002  62.069             16    31
4     2  1093  74.155139  -16.600000  17.749001  62.069             46    28

In [50]:
data['day_length'] = day_length(data['Julian Center'], data['lat']) #Calculate day length with above function

data['Wm'] = (4.95*np.e**(0.062*data['PRISM_Temp']))/100 #Saturated water vapour density formula from (Hamon, 1961)

data['PET'] = 13.97*data['days']*(data['day_length']**2)*data['Wm'] #Calculate PET

data['surplus'] = data['PRISM_Ppt'] - data['PET'] #Calculate surplus

data.head()

month  site        SWE  PRISM_Temp  PRISM_Ppt     lat  Julian Center  days  \
0    10  1093   9.873226   -6.295001  23.601002  62.069            289    31   
1    11  1093  24.565429  -17.150002  20.528002  62.069            320    30   
2    12  1093  44.648986  -20.220001  17.347000  62.069            350    31   
3     1  1093  58.554608  -21.640001  20.372002  62.069             16    31   
4     2  1093  74.155139  -16.600000  17.749001  62.069             46    28   

   day_length        Wm        PET    surplus  
0    0.837042  0.033505  10.166151  13.434851  
1    0.590636  0.017093   2.499062  18.028940  
2    0.432497  0.014130   1.144672  16.202328  
3    0.511528  0.012940   1.466286  18.905716  
4    0.736681  0.017686   3.754416  13.994585

In [51]:
data['PREV_SWE'] = np.NaN #Add column for previous SWE

for i in range(1, len(data)): #Iterate through all data
    data.loc[i, 'PREV_SWE'] = data.loc[i-1, 'SWE'] #Add previous SWE to cell

data.loc[0, 'PREV_SWE'] = data.iloc[-1]['SWE'] #Add the last value

data.head()

month  site        SWE  PRISM_Temp  PRISM_Ppt     lat  Julian Center  days  \
0    10  1093   9.873226   -6.295001  23.601002  62.069            289    31   
1    11  1093  24.565429  -17.150002  20.528002  62.069            320    30   
2    12  1093  44.648986  -20.220001  17.347000  62.069            350    31   
3     1  1093  58.554608  -21.640001  20.372002  62.069             16    31   
4     2  1093  74.155139  -16.600000  17.749001  62.069             46    28   

   day_length        Wm        PET    surplus   PREV_SWE  
0    0.837042  0.033505  10.166151  13.434851   2.282701  
1    0.590636  0.017093   2.499062  18.028940   9.873226  
2    0.432497  0.014130   1.144672  16.202328  24.565429  
3    0.511528  0.012940   1.466286  18.905716  44.648986  
4    0.736681  0.017686   3.754416  13.994585  58.554608

In [52]:
#Drop unnecessary columns and rename columns
data.drop(['lat', 'Julian Center', 'days', 'day_length', 'Wm', 'PET', 'PRISM_Ppt'], axis=1, inplace=True)
data = data.rename(columns={'SWE': 'SNOTEL_SWE', 'PRISM_Temp': 'PRISM_T', 'site': 'ST_ID'}) 
data.columns = data.columns.str.upper() #Upper case
data = data.set_index('MONTH') #Set index as month
data['CODE'] =1 #Add column 
data = data[['ST_ID', 'CODE', 'SURPLUS', 'PRISM_T', 'SNOTEL_SWE', 'PREV_SWE']] #Reorder columns
data.head()

ST_ID  CODE    SURPLUS    PRISM_T  SNOTEL_SWE   PREV_SWE
MONTH                                                          
10      1093     1  13.434851  -6.295001    9.873226   2.282701
11      1093     1  18.028940 -17.150002   24.565429   9.873226
12      1093     1  16.202328 -20.220001   44.648986  24.565429
1       1093     1  18.905716 -21.640001   58.554608  44.648986
2       1093     1  13.994585 -16.600000   74.155139  58.554608

In [53]:
from google.colab import files #Save to csv and download
data.to_csv('nlr_inputs_comb.csv', encoding = 'utf-8-sig') 
files.download('nlr_inputs_comb.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [54]:
#This code cell will create a random sample (by site to use as training data)
sites = data['ST_ID'].unique() #Get list of all sites
num = int(len(data['ST_ID'].unique())*0.4) #Determine number of sites to sample, 40% of sites are sampled
d = np.random.choice(sites, num) #Randomly select sites

data_sample = data

for i in d: #Iterate through and remove sites that are selected
  data_sample = data_sample[data_sample.ST_ID != i]

#This creates a new dataframe with 60% of the sites remaining
data_sample.head()

ST_ID  CODE    SURPLUS    PRISM_T  SNOTEL_SWE    PREV_SWE
MONTH                                                           
10      1268     1  44.551244  -3.910000   20.903790    0.524463
11      1268     1  20.997427 -13.120001   64.304333   20.903790
12      1268     1  22.502537 -14.360001  113.736694   64.304333
1       1268     1  23.993851 -16.465000  148.784597  113.736694
2       1268     1  32.936907 -13.220000  194.411150  148.784597

In [55]:
data_sample.to_csv('nlr_inputs_base.csv', encoding = 'utf-8-sig') #Save and download this as well
files.download('nlr_inputs_base.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

The next part of this code will extract the temperature and precipitation from every raster cell within the HUC 6 watershed and calculate the surplus. It will create a zip file of this data for each month and download the file. 

In [56]:
import geopandas as gpd
import rioxarray as rxr
from shapely.geometry import mapping

#Read in HUC 6 boundary
huc6 = gpd.read_file('https://github.com/samsamsam34/AKSnowModel/blob/d9a28bc184bcc61a78e2ec50703acb35c5ef5c5a/SiteBoundaryHUC6.geojson?raw=true')
huc6

Expecting property name enclosed in double quotes: line 1 column 2 (char 1)


OBJECTID                                   tnmid metasourceid  \
0         1  {4668D3D5-50BC-41B2-A100-72F60B3AE14A}         None   

  sourcedatadesc sourceoriginator sourcefeatureid       loaddate  \
0           None             None            None  1616419983000   

  referencegnis_ids   areaacres   areasqkm states    huc6          name  \
0              None  28560754.3  115581.37  AK,CN  190803  Tanana River   

   Shape_Length  Shape_Area                                           geometry  
0     51.193671   21.163393  POLYGON ((-147.83726 65.70686, -147.83726 65.7...

In [65]:
#Same function as above except we're extracting at every pixel instead of only at specific SNOTEL sites
def extractTemp(filepath, month):
  drv = gdal.GetDriverByName('GTiff')
  ds_in = gdal.Open(filepath)

  tifName = 'projTemp' + str(month).zfill(2) + '.tif'

  ds_out = drv.CreateCopy(tifName, ds_in)
  srs = osr.SpatialReference()
  srs.ImportFromEPSG(4269) #NAD 83
  ds_out.SetProjection(srs.ExportToWkt())
  ds_in = None
  ds_out = None

  input = rxr.open_rasterio(tifName,masked=True).squeeze()

  temp_clipped = input.rio.clip(huc6.geometry.apply(mapping),huc6.crs)

  temp_clipped.rio.to_raster('HUC6_Temp.tif')

  #Convert raster to dataframe, keep lat, lon, and value
  rds = rxr.open_rasterio(
    "HUC6_Temp.tif",
  )
  rds = rds.squeeze().drop("spatial_ref").drop("band")
  rds.name = "Temp"
  raster_df = rds.to_dataframe().reset_index()
  
  return raster_df




In [66]:
#Same as above but for precip data
def extractPpt(filepath, month):
  drv = gdal.GetDriverByName('GTiff')
  ds_in = gdal.Open(filepath)

  tifName = 'projPpt' + str(month).zfill(2) + '.tif'

  ds_out = drv.CreateCopy(tifName, ds_in)
  srs = osr.SpatialReference()
  srs.ImportFromEPSG(4269) #NAD 83
  ds_out.SetProjection(srs.ExportToWkt())
  ds_in = None
  ds_out = None

  input = rxr.open_rasterio(tifName,masked=True).squeeze()

  ppt_clipped = input.rio.clip(huc6.geometry.apply(mapping),huc6.crs)

  ppt_clipped.rio.to_raster('HUC6_Ppt.tif')

  #Convert raster to dataframe, keep lat, lon, and value
  rds = rxr.open_rasterio(
    "HUC6_Ppt.tif",
  )
  rds = rds.squeeze().drop("spatial_ref").drop("band")
  rds.name = "Ppt"
  raster_df = rds.to_dataframe().reset_index()
  
  return raster_df


In [67]:
#This function does the surplus calculation for a given month
def compileData(month): #Month is an integer
  tempFile = '/content/ak_tmean_1981_2010.' + str(month).zfill(2) +'.txt' #Extract temp and precip data from PRISM
  pptFile = '/content/ak_ppt_1981_2010.' + str(month).zfill(2) +'.txt'
  tempVals = extractTemp(tempFile, month)
  pptVals = extractPpt(pptFile, month)

  combined = pd.merge(tempVals, pptVals,  how='left', left_on=['x','y'], right_on = ['x','y']) #Merge temp and precip
  combined = combined[combined.Temp != -9999.0] #Drop no data (which is stored as -9999)

  J = julian.loc[julian['month']==month]['Julian Center'][month-1] #Calculate day length -- same as above
  days = julian.loc[julian['month']==month]['days'][month-1]
  combined['day_length'] = day_length(J, combined['y'])
  combined['Wm'] = (4.95*np.e**(0.062*combined['Temp']))/100
  combined['PET'] = 13.97*days*(combined['day_length']**2)*combined['Wm']
  combined['surplus'] = combined['Ppt'] - combined['PET'] #Calculate surplus --same as above

  #Same code as above, just reformatting the dataframe
  combined.drop(['day_length', 'Wm', 'PET', 'Ppt'], axis=1, inplace=True)
  combined['MONTH'] = month
  combined = combined.rename(columns={'Temp': 'PRISM_T', 'site': 'ST_ID'}) 
  combined.columns = combined.columns.str.upper()
  combined = combined.set_index('MONTH')
  combined['CODE'] =1
  combined = combined[['Y', 'X', 'CODE', 'SURPLUS', 'PRISM_T']]
  return combined


In [68]:
jan = compileData(1) #Check out the data for January 
jan.head()

Y           X  CODE    SURPLUS    PRISM_T
MONTH                                                   
1      65.716667 -147.891667     1  22.732487 -16.870001
1      65.716667 -147.883333     1  22.868646 -16.650002
1      65.716667 -147.875000     1  23.022102 -16.560001
1      65.716667 -147.866667     1  23.188456 -16.675001
1      65.716667 -147.858333     1  23.249282 -16.645000

In [69]:
from zipfile import ZipFile

#Produce output file for each month and zip into one file, this may take a while to run
zipObj = ZipFile('nlr_inputs.zip', 'w') #Open a zip object
for i in [10,11,12,1,2,3,4,5,6,7,8,9]: #Iterate through months, sorted by wateryear
  c = compileData(i) #Calculate surplus and produce dataframe with above function

  csvName = 'nlr_input' + str(i).zfill(2) + '.csv' #Define name for csv
  c.to_csv(csvName, encoding = 'utf-8-sig') #Save dataframe to csv
  zipObj.write(csvName) #Add file to zip object

zipObj.close() #Close zip object
files.download('nlr_inputs.zip') #Download zip file


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Now that all of the input data is collected and downloaded, open up the AK_SWE_NLR script in R. There's no need to move this zip file out of your downloads folder. 